In [1]:
import pandas as pd
import numpy as np
import openpyxl as opxl
import os.path
import pycountry
import pycountry_convert as pc
import datetime as dt
import json
import os.path

In [2]:
def importExcelSheets():
    magento = pd.read_excel('database_sheets/magento_may.xlsx')
    new_magento = pd.read_excel('database_sheets/magento_july.xlsx')
    magento_sept = pd.read_excel('database_sheets/magento_sept.xlsx')
    lot_master = pd.read_excel('database_sheets/lot_master.xlsx', dtype = object)
    prms = pd.read_excel('database_sheets/prms.xlsx')
    unspsc_codes = pd.read_excel('database_sheets/unspsc_codes.xlsx')
    unspsc_codes.columns = unspsc_codes.iloc[0]
    origin = pd.read_excel('database_sheets/country_of_origin.xlsx', dtype=object)
    pd.set_option("max_rows", None)
    pd.set_option("max_columns", None)
    return [magento, new_magento, lot_master, prms, unspsc_codes, origin, magento_sept]

In [3]:
def tidyDescription(desc):
    desc = desc.replace('&TRADE', '')
    desc = desc.replace('Â®', '')
    desc = desc.replace('Î¼', '')
    desc = desc.replace('& Growâ„¢', '')
    desc = desc.replace('â‰', '')
    desc = desc.replace('&Beta', '')
    desc = desc.replace('Â‰¥', '')
    desc = desc.replace('Â', '')
    desc = desc.replace('<em>', '')
    desc = desc.replace('</em>', '')
    desc = desc.replace('®','')
    desc = desc.replace('<F128>','')
    desc = desc.replace('<130>','')
    desc = desc.replace('<F255>','')
    desc = desc.replace('&deg;', '°')
    desc = desc.replace('deg ', '°')
    if desc.endswith(','):
        desc = desc[:len(desc)-1]
    return desc

In [4]:
database_sheets = importExcelSheets()

In [23]:
pd.set_option("max_rows")

1                                                NaN  \
0  The buttons below should allow you to hide/sho...   
1                                                NaN   
2                                                NaN   
3                                                NaN   

1                                      Supplier Name  \
0                                      Supplier Info   
1                                      Supplier Name   
2   Name of Supplier. Only needs to be entered on...   
3                                 MP Biomedicals,LLC   

1                          Email Address for Contact  \
0                                                NaN   
1                          Email Address for Contact   
2   Email of Contact at Supplier who can address ...   
3                              Lisa.bowers@mpbio.com   

1                                      Contact Phone  \
0                                                NaN   
1                                      Contact Phone   
2   Phone number for contact at supplier who can ...   
3                                      (800)854-0530   

1                                 Vendor Part Number  \
0                                        Description   
1                                 Vendor Part Number   
2   Supplier's unique part number to indicate thi...   
3                                                NaN   

1                           40 Character Description  \
0                                                NaN   
1                           40 Character Description   
2   40 Characters only (All in UPPER CASE). Stand...   
3                                                NaN   

1                               Enhanced Description  \
0                                                NaN   
1                               Enhanced Description   
2   You have a maximum of 300 characters here to ...   
3                                                NaN   

1                           Purchase Unit of Measure  \
0                                    Purchasing Info   
1                           Purchase Unit of Measure   
2   The unit of measure that VWR should purchase ...   
3                                                NaN   

1                                     Minimum Order?  \
0                                                NaN   
1                                     Minimum Order?   
2   Is there a minimum order that VWR must meet i...   
3                                                NaN   

1                                       Vendor Price  \
0                                                NaN   
1                                       Vendor Price   
2   Price VWR will pay for the purchasing unit of...   
3                                                NaN   

1                                    Vendor Currency  \
0                                                NaN   
1                                    Vendor Currency   
2   Currency that VWR will pay supplier. USD or CAD.   
3                                                NaN   

1                                Future Vendor Price  \
0                                                NaN   
1                                Future Vendor Price   
2   If after 9/15 of the current year, VWR requir...   
3                                                NaN   

1                    Future Pricing Effectivity Date  \
0                                                NaN   
1                    Future Pricing Effectivity Date   
2   The date the future pricing will be effective...   
3                                                NaN   

1                             US Item Category Group  \
0                                        Warehousing   
1                             US Item Category Group   
2   Item Category Group determines DFS status, am...   
3                                                NaN   

1                             CA Item Category Group  \
0         

In [6]:
from difflib import SequenceMatcher

In [5]:
from Spider_Pubchem import runMerged
# from Spider import task1
# from difflib import SequenceMatcher

def chooseSearchName(sku, magento):
    product_info = magento.loc[magento['sku'] == sku]

    search_name = ''

    if not product_info.empty:
        cas_number = product_info['cas_number'].values[0]

        if type(cas_number) == str and len(cas_number) > 0:
            search_name = cas_number
        else:
            pack_size_joined = product_info['pack_size_joined'].values[0]
            name = product_info['name'].values[0]
            if type(name) == str:
                if type(pack_size_joined) == str:
                    name = name.replace(pack_size_joined, '')
                search_name = name

    return search_name

def getPubchemData(sku, magento):
    search_name = chooseSearchName(sku, magento)
    if len(search_name) > 0:
        runMerged([search_name])

        try:
            with open('Pubchem/result.json', 'r') as f:
                data = json.load(f)

            for item in data:
                if item['search_name'] == search_name:
                    return item
        except:
            print('pubchem error...')

    return None

# def chooseDataAbcam(data, product_info):
#     if not product_info.empty:
#         for item in data:
#             if item['search_name'] == product_info['cas_number'].values[0]:
#                 return item
#             else:
#                 antibody_type = product_info['antibody_type'].values[0]
#                 antibody_type = str(antibody_type)
#                 if 'Polyclonal' in antibody_type or 'polycolnal' in antibody_type:
#                     antibody_type = 'Polyclonal'
#                 elif 'Monoclonal' in antibody_type or 'monoclonal' in antibody_type:
#                     antibody_type = 'Monoclonal'
#                 else:
#                     antibody_type = ''

#                 similarity = SequenceMatcher(None, item['search_name'], item['product_name']).ratio()

#                 if item['Clonality'] == antibody_type and similarity > 0.6:
#                     return item

#     return None

# def getAbcamData(sku, magento):
#     search_name = chooseSearchName(sku, magento)
#     product_info = magento.loc[magento['sku'] == sku]
#     if os.path.exists('Abcam/'+str(search_name)+'.json'):
#         with open('Abcam/'+str(search_name)+'.json', 'r') as f:
#             data = json.load(f)
        
#         return chooseDataAbcam(data, product_info)
#     elif len(search_name) > 0:
#         search_name = search_name.replace('/', '')
#         task1('Abcam', [search_name])
#         # print(os.path.exists('Abcam/'+str(search_name)+'.json'))
#         if os.path.exists('Abcam/'+str(search_name)+'.json'):
#             with open('Abcam/'+str(search_name)+'.json', 'r') as f:
#                 data = json.load(f)
            
#             return chooseDataAbcam(data, product_info)
#         else:
#             return None

#     else:
#         return None

In [6]:
def attributeLookup(attribute, product_info, product_info_sept, prms_info, lot_info, unspsc_info, origin_info, abcam_info, sku, magento):

    if attribute == 'Form':
        try:
            pubchem_data = getPubchemData(sku, magento)
            # pubchem_data = None # replace this
            if not pubchem_data == None:
                form = pubchem_data['Color/Form']
                return form + " | pulled from Pubchem"
        except:
            print('Pubchem Error')

    if not prms_info.empty:
        storage_condition = prms_info['Storage Temp'].values[0]
        ship_temp = prms_info['Ship Temp'].values[0]
        # un_num = prms_info['UN#'].values[0]
        
        if storage_condition == 'AM':
            storage_condition = 'Room Temperature'
            storage_code = 'GWN4'
        elif storage_condition == 'RF':
            storage_condition = 'Refrigerated'
            storage_code = 'RFC2'
        elif storage_condition == 'FR':
            storage_condition = 'Frozen'
            storage_code = 'DFD1'
        else:
            storage_code = ''
            
        if ship_temp == 'AM':
            ship_temp = 'Ambient'
        elif ship_temp == 'CP':
            ship_temp = 'Cold Pack'
        elif ship_temp == 'DI':
            ship_temp = 'Dry Ice'
    else:
        storage_condition = ''
        storage_code = ''
        ship_temp = ''
        # un_num = ''
        
    if not lot_info.empty:
        creation_date = np.datetime64(lot_info['Creation date -'].values[0])
        expiration_date = np.datetime64(lot_info['Expiration date -'].values[0])
        shelf_life = expiration_date - creation_date
        shelf_life = shelf_life.astype('timedelta64[D]')/np.timedelta64(1, 'D')
    else:
        shelf_life = ''
        
    if not origin_info.empty:
        country_of_origin = origin_info.loc[origin_info['Expiration date -'] == max(origin_info['Expiration date -'].values)]['Country of Origin'].values[0]
    elif not prms_info.empty:
        country_of_origin = prms_info['Country of Origin (most recent lot)'].values[0]
    elif not lot_info.empty:
        country_of_origin = lot_info['Country of Origin'].values[0]
    else:
        country_of_origin = ''

    if not product_info_sept.empty:
        antibody_type = product_info_sept['antibody_type'].values[0]
        antibody_type = str(antibody_type)
        if 'Polyclonal' in antibody_type or 'polycolnal' in antibody_type:
            antibody_type = 'Polyclonal'
        elif 'Monoclonal' in antibody_type or 'monoclonal' in antibody_type:
            antibody_type = 'Monoclonal'
        else:
            antibody_type = ''

        keywords = product_info_sept['keywords'].values[0]
        keywords = str(keywords)
        if 'Primary' in keywords or 'primary' in keywords:
            keywords = 'Primary'
        elif 'Secondary' in keywords or 'secondary' in keywords:
            keywords = 'Secondary'
        else:
            keywords = ''

        short_desc = product_info_sept['short_description'].values[0]
        short_desc = tidyDescription(str(short_desc))

        application_notes = product_info_sept['application_notes'].values[0]
        application_notes = str(application_notes)
        if 'strain' in application_notes or 'Strain' in application_notes:
            application_notes = 'Strain'
        elif 'genotype' in application_notes or 'Genotype' in application_notes:
            application_notes = 'Genotype'
        else:
            application_notes = ''

        host = product_info_sept['host'].values[0]

        un_number = product_info_sept['un_number'].values[0]
        if not str(un_number).startswith('UN'):
            un_number = ''

    else:
        antibody_type = ''
        keywords = ''
        short_desc = ''
        application_notes = ''
        host = ''
        un_number = ''

    if not abcam_info == None:
        purity = abcam_info['Purity'] + " | pulled from Abcam"
        immunogen = abcam_info['Immunogen'] + " | pulled from Abcam"
        isotype = abcam_info['Isotype'] + " | pulled from Abcam"
        function = abcam_info['Function'] + " | pulled from Abcam"
        concentration = abcam_info['Concentration'] + " | pulled from Abcam"
        clonality = abcam_info['Clonality'] + " | pulled from Abcam"
        try:
            host_species = abcam_info['Host species'] + " | pulled from Abcam"
        except:
            host_species = abcam_info['Host Species'] + " | pulled from Abcam"
        clone_number = abcam_info['Clone number'] + " | pulled from Abcam"
        light_chain_type = abcam_info['Light chain type'] + " | pulled from Abcam"
        species_reactivity = abcam_info['Species reactivity'] + " | pulled from Abcam"
    else:
        purity = ''
        immunogen = ''
        isotype = ''
        function = ''
        concentration = ''
        clonality = ''
        host_species = ''
        clone_number = ''
        light_chain_type = ''
        species_reactivity = ''

    if type(light_chain_type) == str and len(light_chain_type) > 0:
        light_chain_type = 'Chains'
    else:
        light_chain_type = ''
        
    attribute_dict = {}

    if not product_info_sept.empty:
        print("sku: {}, attribute: {}".format(sku, attribute))
        attribute_dict['Sterility'] = product_info_sept['sterilization_of_solutions'].values[0]
        attribute_dict['Synonym'] = product_info_sept['alternate_names'].values[0]
        attribute_dict['Formula Weight'] = product_info_sept['molecular_weight'].values[0]
        attribute_dict['For Use With'] = product_info_sept['application_notes'].values[0]
        attribute_dict['Linear Formula'] = product_info_sept['molecular_formula'].values[0]
        attribute_dict['absorbance'] = product_info_sept['uv_visible_absorbance'].values[0]
        attribute_dict['Absorbance'] = product_info_sept['uv_visible_absorbance'].values[0]
        attribute_dict['Ignition Point'] = product_info_sept['auto_ignition'].values[0]
        attribute_dict['Enzyme'] = product_info_sept['protein_or_enzyme_type'].values[0]
        attribute_dict['Validated Application'] = product_info_sept['application_notes'].values[0]
        attribute_dict['Research Category'] = product_info_sept['key_applications'].values[0]
        attribute_dict['Conjugate'] = product_info_sept['conjugate'].values[0]
        attribute_dict['Grade'] = product_info_sept['grade'].values[0]
        attribute_dict['Protein Family'] = product_info_sept['protein_or_enzyme_type'].values[0]
        attribute_dict['pH'] = product_info_sept['ph'].values[0]
        attribute_dict['Sample Size'] = product_info_sept['pack_size_joined'].values[0]
        attribute_dict['Molecular Formula'] = product_info_sept['molecular_formula'].values[0]
        attribute_dict['Molecular Weight (g/mol)'] = product_info_sept['molecular_weight'].values[0]
        attribute_dict['Sample Volume'] = product_info_sept['pack_size_joined'].values[0]
        attribute_dict['Density'] = product_info_sept['density'].values[0]
        attribute_dict['Sufficient For'] = product_info_sept['key_applications'].values[0]
        attribute_dict['Flash Point'] = product_info_sept['flash_point'].values[0]
        attribute_dict['Packaging Quantity'] = product_info_sept['pack_size_joined'].values[0]
        attribute_dict['Melting Point'] = product_info_sept['melting_point'].values[0]
        attribute_dict['pH Range'] = product_info_sept['ph'].values[0]
        attribute_dict['Sensitivity'] = product_info_sept['sensitivity'].values[0]
        attribute_dict['Test Sensitivity'] = product_info_sept['sensitivity'].values[0]
        attribute_dict['Monoclonal or Polyclonal'] = antibody_type
        attribute_dict['Formulation'] = product_info_sept['formulation'].values[0]
        attribute_dict['Green Features'] = 'NA'
        attribute_dict['CAS'] = product_info_sept['cas_number'].values[0]
        attribute_dict['Melting Temp_Begin'] = product_info_sept['melting_point'].values[0]
        attribute_dict['Primary or Secondary'] = keywords
        attribute_dict['Description'] = short_desc
        attribute_dict['Strain or Genotype'] = application_notes
        attribute_dict['Shipping Condition'] = ship_temp
        attribute_dict['Host Species'] = host
        attribute_dict['CAS Max %'] = '100'
        attribute_dict['Molecular Weight of Antigen'] = product_info_sept['molecular_weight'].values[0]
        attribute_dict['Solubility'] = product_info_sept['solubility'].values[0]
        attribute_dict['Boiling Point'] = product_info_sept['boiling_point'].values[0]
        attribute_dict['UN Number'] = un_number
        attribute_dict['Sterility'] = product_info_sept['sterility'].values[0]
        attribute_dict['CAS Min %'] = '0'
        attribute_dict['Antibody Molecular Weight'] = product_info_sept['molecular_weight'].values[0]
        attribute_dict['Origin'] = product_info_sept['concentration'].values[0]
        attribute_dict['Boiling Range'] = product_info_sept['boiling_point'].values[0]
        attribute_dict['For Use With (Application)'] = product_info_sept['upsell_position'].values[0]

    if not prms_info.empty:
        attribute_dict['Content And Storage'] = storage_condition
        attribute_dict['Storage Requirements'] = storage_condition
        attribute_dict['Storage'] = storage_condition

    if not lot_info.empty:
        attribute_dict['Manufacturing Origin'] = country_of_origin
        attribute_dict['Country of Origin'] = country_of_origin

    if not abcam_info == None:
        attribute_dict['Purity'] = purity
        attribute_dict['Purity Grade Notes'] = purity
        attribute_dict['Sub Class Isotype'] = isotype
        attribute_dict['Isotype'] = isotype
        attribute_dict['Key Functions'] = function
        attribute_dict['Target Isotype'] = isotype
        attribute_dict['Glucose Concentration'] = concentration
        attribute_dict['Clonality'] = clonality
        attribute_dict['Host abrv'] = host_species
        attribute_dict['Percent Purity'] = purity
        attribute_dict['Concentration'] = concentration
        attribute_dict['Host Cell'] = host_species
        attribute_dict['Clone ID'] = clone_number
        attribute_dict['Concentration Ratio'] = concentration
        attribute_dict['Chains or Fragments'] = light_chain_type
        attribute_dict['Concentration or Composition (by Analyte or Components)'] = concentration
        attribute_dict['Concentration or Composition Notes'] = concentration
        attribute_dict['Endotoxin Concentration'] = concentration
        attribute_dict['Target Function'] = function
        attribute_dict['Purity or Quality Grade'] = purity
        attribute_dict['Reactivity'] = species_reactivity
        attribute_dict['BIS MSB Concentration'] = concentration
        attribute_dict['Enzyme Function'] = function

    
    if attribute in attribute_dict:
        return attribute_dict[attribute]
    else:
        return ''

def fillFisher_Enrichment(filename, magento, new_magento, lot_master, prms, magento_sept, unspsc_codes, origin):
    authoring_file = pd.ExcelFile(filename)

    authoring = pd.read_excel(authoring_file, 'Core_Content', dtype=object)
    authoring.columns = authoring.iloc[2]
    authoring.columns = [i.strip() for i in authoring.columns]

    attributes = pd.read_excel(authoring_file, 'Category_Attributes', dtype=object)
    attributes.columns = attributes.iloc[2]
    attributes.columns = [i.strip() for i in attributes.columns]
        
    for i in range(3, len(authoring)):
        sku = authoring['manufacturerPartNumber'][i]
        product_info = magento.loc[magento['sku'] == sku]
        product_info_sept = magento_sept.loc[magento_sept['sku'] == sku]
        prms_info = prms.loc[prms['SKU'] == sku]
        if not product_info.empty:
            name = product_info['name'].values[0]
            short_description = product_info['short_description'].values[0]
            description = product_info['description'].values[0]
            image = product_info['base_image'].values[0]
            keywords = product_info['meta_keywords'].values[0]
            pack_size_joined = product_info['pack_size_joined'].values[0]
            
            if type(pack_size_joined) == str:
                authoring['productTitle'][i] = name.replace(pack_size_joined, '')
            else:
                authoring['productTitle'][i] = name
                
            authoring['skuDifferentiatorText'][i] = name
            authoring['teaserText'][i] = short_description
            authoring['productFeatures'][i] = description
            authoring['Image'][i] = image
            authoring['keywords'][i] = keywords

        # if not product_info_sept.empty:

        
        if not prms_info.empty:
            un_number = prms_info['UN#'].values[0]
            
            authoring['alerts'][i] = un_number
    
    for i in range(3, len(attributes)-1):
        sku = attributes['manufacturerPartNumber'][i]
        product_info = new_magento.loc[new_magento['sku'] == sku]
        product_info_sept = magento_sept.loc[magento_sept['sku'] == sku]
        prms_info = prms.loc[prms['SKU'] == sku]
        lot_info = lot_master.loc[lot_master['Product number'] == sku]
        unspsc_info = unspsc_codes.loc[unspsc_codes['Part Number'] == sku]
        origin_info = origin.loc[origin['Product number'] == sku]
        
        attribute_name = attributes['Attribute_Name'][i]
        
        # abcam_info = getAbcamData(sku, magento_sept)
        abcam_info = None # replace this

        attributes['Values'][i] = attributeLookup(attribute_name, product_info, product_info_sept, prms_info, lot_info, unspsc_info, origin_info, abcam_info, sku, magento)
        # add this back

    wb_enrichment = opxl.load_workbook(filename)
    core_content = wb_enrichment['Core_Content']
    i = 3
    for row in core_content.iter_rows(min_row=5):
        for j in range(len(authoring.columns)):
            row[j].value = authoring.iloc[i, j]
        i = i+1
    
    attribute_sheet = wb_enrichment['Category_Attributes']
    i = 3
    for row in attribute_sheet.iter_rows(min_row=5):
        if i < len(attributes):
            row[11].value = attributes['Values'][i]
        else:
            break
        i = i+1

    wb_enrichment.save('outputs/enrichment_outputs/fisher_enrichment_output.xlsx')
    # wb_enrichment.save('../../outputs/old_product_outputs/fisher_enrichment_output.xlsx')

In [18]:
authoring_file = pd.ExcelFile('input_sheets/fisher_enrichment_sample.xlsx')

authoring = pd.read_excel(authoring_file, 'Core_Content', dtype=object)

attributes = pd.read_excel(authoring_file, 'Category_Attributes', dtype=object)

# authoring.columns = authoring.iloc[2]
# authoring.columns = [i.strip() for i in authoring.columns]
# authoring.columns = authoring.iloc[2]
authoring.columns = range(len(authoring.columns))
attributes.columns = range(len(attributes.columns))

attributes.iloc[:3]

0              1                       2  \
0  Optional - for reference only.  Do not alter.      DO NOT SORT SHEET.   
1                             NaN            NaN           Do not alter.   
2                     Family_Code   Product_Code  manufacturerPartNumber   

               3                  4               5                        6  \
0  Do not alter.                NaN   Do not alter.             Do not alter   
1            NaN      Do not alter.             NaN                      NaN   
2   MTS_Leafnode  Taxonomy_Category  Classification  classificationattribute   

                7                      8             9  \
0             NaN                    NaN  Do not alter   
1   Do not alter.          Do not alter.           NaN   
2  Attribute_Name  Attribute_Description   Multivalued   

                            10                    11  \
0                Do not alter.  ENGLISH values only.   
1  REQUIRED WHERE MARKED "Yes"                   NaN   
2                     Required                Values   

                         12                        13  \
0  Ignore grayed-out cells.  Ignore grayed-out cells.   
1                       NaN                       NaN   
2              MultiValue_1              MultiValue_2   

                         14                        15                   16  \
0  Ignore grayed-out cells.  Ignore grayed-out cells.                  NaN   
1                       NaN                       NaN                  NaN   
2              MultiValue_3              MultiValue_4  Value_Not_Available   

                     17                   18                   19  \
0                   NaN                  NaN                  NaN   
1  SPANISH values only.  GERMAN values only.  FRENCH values only.   
2                    ES                   DE                   FR   

                     20                  21  
0                   NaN  Internal use only.  
1  ITALIAN values only.                 NaN  
2                    IT              action

In [7]:
fillFisher_Enrichment('input_sheets/fisher_enrichment_sample.xlsx', database_sheets[0], database_sheets[1], database_sheets[2], database_sheets[3], database_sheets[6], database_sheets[4], database_sheets[5])

sku: 091760422, attribute: Additive
sku: 091760422, attribute: Boiling Point
sku: 091760422, attribute: Calibration Type
sku: 091760422, attribute: Capacity
sku: 091760422, attribute: Cell Permeability
sku: 091760422, attribute: Cell Type
sku: 091760422, attribute: Chromagen Type
sku: 091760422, attribute: Classification
sku: 091760422, attribute: Closure Type
sku: 091760422, attribute: Color
sku: 091760422, attribute: Compatibility
sku: 091760422, attribute: Concentration
sku: 091760422, attribute: Conjugate
sku: 091760422, attribute: Content And Storage
sku: 091760422, attribute: Depth (Metric)
sku: 091760422, attribute: Description
sku: 091760422, attribute: Detection Method
sku: 091760422, attribute: Diameter (Metric)
sku: 091760422, attribute: Dilution
sku: 091760422, attribute: Dimensions
sku: 091760422, attribute: Emission
sku: 091760422, attribute: Endotoxin Level
sku: 091760422, attribute: Enzyme
sku: 091760422, attribute: Excitation
sku: 091760422, attribute: Excitation/Emiss

In [14]:
authoring

Comments  \
0    Data provided here will not be shown on the web.   
1                                                 NaN   
2                                            Comments   
3                                                 NaN   
4                                                 NaN   
5                                                 NaN   
6                                                 NaN   
7                                                 NaN   
8                                                 NaN   
9                                                 NaN   
10                                                NaN   
11                                                NaN   
12                                                NaN   
13                                                NaN   
14                                                NaN   
15                                                NaN   
16                                                NaN   
17                                                NaN   
18                                                NaN   
19                                                NaN   
20                                                NaN   
21                                                NaN   
22                                                NaN   
23                                                NaN   
24                                                NaN   
25                                                NaN   
26                                                NaN   
27                                                NaN   
28                                                NaN   
29                                                NaN   
30                                                NaN   
31                                                NaN   
32                                                NaN   
33                                                NaN   
34                                                NaN   
35                                                NaN   
36                                                NaN   
37                                                NaN   
38                                                NaN   
39                                                NaN   
40                                                NaN   
41                                                NaN   
42                                                NaN   
43                                                NaN   
44                                                NaN   
45                                                NaN   
46                                                NaN   
47                                                NaN   
48                                                NaN   
49                                                NaN   
50                                                NaN   
51                                                NaN   
52                                                NaN   
53                                                NaN   
54                                                NaN   
55                                                NaN   
56                                                NaN   
57                                                NaN   
58                                                NaN   
59                                                NaN   
60                                                NaN   
61                                                NaN   
62                                                NaN   
63                                                NaN   
64                                                NaN   
65                                                NaN   
66                                                NaN   
67                                                NaN   
68                                                NaN   
69                                                NaN  

In [17]:
display(vwr_filled)

1                                                  NaN  \
0    The buttons below should allow you to hide/sho...   
1                                                  NaN   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
5                                                  NaN   
6                                                  NaN   
7                                                  NaN   
8                                                  NaN   
9                                                  NaN   
10                                                 NaN   
11                                                 NaN   
12                                                 NaN   
13                                                 NaN   
14                                                 NaN   
15                                                 NaN   
16                                                 NaN   
17                                                 NaN   
18                                                 NaN   
19                                                 NaN   
20                                                 NaN   
21                                                 NaN   
22                                                 NaN   
23                                                 NaN   
24                                                 NaN   
25                                                 NaN   
26                                                 NaN   
27                                                 NaN   
28                                                 NaN   
29                                                 NaN   
30                                                 NaN   
31                                                 NaN   
32                                                 NaN   
33                                                 NaN   
34                                                 NaN   
35                                                 NaN   
36                                                 NaN   
37                                                 NaN   
38                                                 NaN   
39                                                 NaN   
40                                                 NaN   
41                                                 NaN   
42                                                 NaN   
43                                                 NaN   
44                                                 NaN   
45                                                 NaN   
46                                                 NaN   
47                                                 NaN   
48                                                 NaN   
49                                                 NaN   
50                                                 NaN   
51                                                 NaN   
52                                                 NaN   
53                                                 NaN   
54                                                 NaN   
55                                                 NaN   
56                                                 NaN   
57                                                 NaN   
58                                                 NaN   
59                                                 NaN   
60                                                 NaN   
61                                                 NaN   
62                                                 NaN   
63                                                 NaN   
64                                                 NaN   
65                                                 NaN   
66                                                 NaN   
67                                                 NaN  